### 练习3. 转账Agent
设计一个 Agent， 能够协助用户完成转账操作

#### 目标
使用 qwen3-32b 模型
1. 向用户收集
    1. 对方姓名（写死只有“张三”存在并返回手机号，其他都不存在）
    2. 对方卡号
    3. 转账金额（只有500）
2. 收集完成后，调用转账接口向对方转账并提示用户转账结果
3. 如果转账失败用户可以重新修改信息并再次发起转账

#### 要求
1. 给 Agent 提供必要的工具，Agent 来决定调用哪个工具。
2. 但是 agent必须要能够正确的用户给的参数来调用对应的方法

#### 场景
1. Agent在接收满足上面 tools要求的情况下， 校验成功转账
2. Agent 在接收不满足上面 tools要求的情况下， 和用户澄清并让用户修改信息。用户修改正确后，可以完成转账。
    1. 余额不足，和用户沟通，用户只能转少于500块
    2. 其他：账号手机号不存在，用户可以手动输入手机号


In [ ]:
import os
from dotenv import load_dotenv

load_dotenv()
base_url = os.getenv('BAILIAN_API_BASE_URL')
api_key = os.getenv('BAILIAN_API_KEY')

### 主题7. Monitoring
目标： 能够观察服务运行情况，结构化的查看 agent、workflow 的每一步运行，学会 debug

TODO：

模型调用tools时会报错，并非流式传输导致

In [ ]:
from langfuse import Langfuse, get_client
import openlit

langfuse = Langfuse(
  secret_key=os.getenv('LANGFUSE_SECRET_KEY'),
  public_key=os.getenv('LANGFUSE_PUBLIC_KEY'),
  host=os.getenv('LANGFUSE_HOST'),
)

langfuse = get_client()
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

print("Starting OpenLit with Langfuse integration...")
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True)

In [ ]:
from agno.agent import Agent, RunResponseEvent
from agno.tools import tool
from agno.memory.v2.db.sqlite import SqliteMemoryDb
from agno.memory.v2.memory import Memory
from agno.storage.sqlite import SqliteStorage
from agno.models.openai.like import OpenAILike
from typing import Optional, Tuple
from dataclasses import dataclass
from enum import Enum

SYSTEM_PROMPT = """
你是一个转账助手，帮助用户完成转账操作。

规则：
1. 系统中只存在"张三"这个用户
2. 最大转账金额为不能超过用户的余额
3. 需要验证收款人姓名、账号和金额
4. 如果转账失败，根据具体错误原因协助用户修改信息：
   - 如果用户不存在，提醒用户检查收款人姓名
   - 如果手机号不匹配，提醒用户确认手机号
   - 如果余额不足，建议用户调整转账金额
5. 如果用户有其他疑问，提供相关帮助

请按照以下步骤操作：
1. 开场先介绍自己是转账助手，询问用户接下来的操作，如果是转账，则按照下面的步骤；如果是其他问题，则提供相关帮助。
2. 收集用户信息：收款人姓名、账号、转账金额
3. 验证信息的正确性，如果信息不完整或错误，引导用户修改
4. 执行转账操作，如果转账成功，告知用户转账成功
5. 如果失败，引导用户修改信息重试
"""

# Mock database for user info
USER_DB = {
    "张三": "13800138000"
}

# UserId for the memories
user_id = "test"
# Database file for memory and storage
db_file = "tmp/agent.db"

model = OpenAILike(
            id="qwen3-32b",
            api_key=api_key,
            base_url=base_url,
            request_params={"extra_body": {"enable_thinking": False}},
        )

# Initialize memory.v2
memory = Memory(
    # Use any model for creating memories
    model=model,
    db=SqliteMemoryDb(table_name="user_memories", db_file=db_file),
)
# Initialize storage
storage = SqliteStorage(table_name="agent_sessions", db_file=db_file)

# Tools for the agent
def get_contact(user_name: str) -> Optional[str]:
    return USER_DB.get(user_name, None)

def get_balance() -> float:
    return 500.0

def reply_to_user(message: str) -> None:
    print(message)

def validate_amount(amount: float) -> bool:
    return amount <= get_balance()

class TransferError(Enum):
    USER_NOT_FOUND = "用户不存在"
    INVALID_PHONE = "手机号不匹配"
    INSUFFICIENT_BALANCE = "余额不足"
    NONE = "无错误"

@dataclass
class TransferResult:
    success: bool
    error: TransferError
    message: str

def validate_transfer(user_name: str, phone: str, amount: float) -> TransferResult:
    """验证转账信息并返回详细结果"""
    if user_name not in USER_DB:
        return TransferResult(False, TransferError.USER_NOT_FOUND, f"收款人 {user_name} 不存在")
    
    if not validate_amount(amount):
        return TransferResult(False, TransferError.INSUFFICIENT_BALANCE, 
                            f"转账金额 {amount} 超过账户余额 {get_balance()}")
    
    if phone != get_contact(user_name):
        return TransferResult(False, TransferError.INVALID_PHONE, 
                            f"手机号 {phone} 与用户信息不匹配")
    
    return TransferResult(True, TransferError.NONE, "验证通过")

def transfer(user_name: str, phone: str, amount: float) -> Tuple[bool, str]:
    """执行转账操作，返回转账结果和详细信息"""
    result = validate_transfer(user_name, phone, amount)
    if result.success:
        return True, "转账成功"
    return False, result.message

agent = Agent(
    model=model,
    tools=[validate_amount, transfer, reply_to_user, get_contact, get_balance],
    instructions=SYSTEM_PROMPT,
    add_datetime_to_instructions=True,
    show_tool_calls=True,
    markdown=True,
    memory=memory,
    enable_user_memories=True,
    storage=storage,
    add_history_to_messages=True,
    # enable_session_summaries=True,
)

In [ ]:
print("转账助手已启动。请开始对话。")
agent.print_response("你好", stream=True, user_id=user_id)
while True:
    user_input = input("用户: ")
    if user_input.lower() in ['exit', 'quit']:
        print("对话结束。")
        break
    if not user_input.strip():
        print("输入不能为空，请重新输入。")
        continue

    agent.print_response(user_input, stream=True, user_id=user_id)

In [ ]:
# langfuse version
print("转账助手已启动。请开始对话。")
agent.print_response("你好", stream=True, user_id=user_id)
while True:
    user_input = input("用户: ")
    if user_input.lower() in ['exit', 'quit']:
        print("对话结束。")
        break
    if not user_input.strip():
        print("输入不能为空，请重新输入。")
        continue

    agent.print_response(user_input, stream=False, user_id=user_id)

In [ ]:
from rich.pretty import pprint

print("Memories about 上个会话:")
pprint(memory.get_user_memories(user_id=user_id))